Recitation notes for November 4th, 2016 by Eric Wong for 15-388/688 Practical Data Science

In [1]:
import matplotlib
matplotlib.use('svg')
%matplotlib inline
import matplotlib.pyplot as plt
plt.style.use('ggplot')
import pandas as pd
import numpy as np

# Hypothesis Testing

Not a lot of new libraries here, in fact everything you need to know is already in the last recitation, and also already in the lecture notes.

In additional to the Gaussian you'll need to work with a T distribution as well. These are all included under `scipy.stats`. Note that the T distribution requires a degree of freedom parameter. 

A reminder that you'll need to use the inverse CDF function; in `scipy.stats` this goes under the name `ppf`. 

In [2]:
# From the last recitation
import scipy.stats as st
st.norm.ppf(0.5); # the value x such that P(X <= x) = 0.5 for X a standard normal random variable
st.t(4).ppf(0.5); # the value t such that P(X <= t) = 0.5 for t a T continuous random variable with 4 degrees of freedom

## Pandas again
You'll need to do various SQL-like queries on your Pandas dataframes. If you are not familiar with it, you can do the following: 

In [3]:
df = pd.DataFrame(np.random.randn(10, 5), columns=['a', 'b', 'c', 'd', 'e'])
df[df["a"] > 0] # gets the subset of the dataframe where the column a is greater than 0
df[(df["a"] >= 1) & (df["b"] < -2)] # gets subset of the dataframe where column a >= 1 and b < -2
df["a"].unique(); # gets all unique values in column "a"

### Pandas Dataframes are array-likes
So you can pass them to `numpy` like any other array. Pandas Series are just 1D numpy arrays. But you can always convert to a numpy array wrapper as soon as you don't need to the dataframe structure anymore. 

In [4]:
np.sum(df, axis=0) # sum along the 0th axis
np.multiply(df,df) # elementwise multiplication
df[["a", "c"]].as_matrix(); # converts the dataframe to a numpy array

# Numpy Tricks & Performance
Again, it's mostly the same numpy (with an initial Pandas to load from the CSV but after processing we immediately just work with numpy arrays). We're letting you use the greatly reduced dataset, so everything works on dense numpy operations. Of course, it is good practice to just write general code that doesn't rely on it. The solution doesn't.

The more advanced algorithms take much longer to run, so its important to write them efficiently. Things like SVM and KMeans are quick and easy even if written inefficiently, but EM algorithms and matrix factorization can take significantly longer even if written well. 

Brief aside from last recitation: `np.newaxis` is actually just a variable with value `None`.

In [5]:
print np.newaxis

None


### Iterating over matrices

Numpy has a list-like indexing method. You don't need to always provide all indices. 

In [6]:
X = np.random.randn(6,10)
X[0] # 0th row
X.T[0] # 0th column
for Xi in X:
    Xi # iterates over each row of X
for Xj  in X.T:
    Xj # iterates over each column of X
for i,Xi in enumerate(X):
    i,Xi # iterates and enumerates each row of X, nicer than doing X[i] within the loop

### Preallocation
Numpy arrays are not like lists. While lists are implemented as unbounded arrays and can be resized somewhat efficiently, numpy arrays are optimized for fixed shape operations. 

Pre-allocate any matrices that you'll use over and over again that don't change (like identity matrices), instead of recreating them every iteration. 

In [7]:
%%timeit
# don't iteratively append rows to a matrix
n = 1000
X = np.ones(n)
for _ in range(200):
    X = np.vstack([X, np.ones(n)])

10 loops, best of 3: 46.4 ms per loop


In [8]:
%%timeit
# Instead, preallocate and assign values
n = 1000
X = np.zeros((200,n))
for i in range(200):
    X[i] = np.ones(n)

1000 loops, best of 3: 1.3 ms per loop


In [9]:
# preallocate matrices that don't change
n = 1000
X = np.random.randn(n,n)
D = np.eye(n)*1e-4
%timeit [X+D for _ in range(10)]
%timeit [X+np.eye(n)*1e-4 for _ in range(10)]

10 loops, best of 3: 40.6 ms per loop
10 loops, best of 3: 96.4 ms per loop


### Computing pairwise distances
Recall from Zico's slides that for KMeans, you need to compute all distances from points to cluster centers. We can compute them naively:

In [10]:
n,m,k = 4,6,2
X = np.random.randn(n,k)
Y = np.random.randn(m,k)

In [11]:
%%timeit
D0 = np.zeros((n,m))
for i, Xi in enumerate(X):
    for j, Yj in enumerate(Y):
        D0[i,j] = ((Xi-Yj)**2).sum()

1000 loops, best of 3: 165 µs per loop


As is the theme with all matrix algebra, it is significantly more efficient to do it in matrix form. 

In [12]:
%%timeit
D = (-2*X.dot(Y.T) + np.sum(X**2,axis=1)[:,None] + np.sum(Y**2, axis=1))

The slowest run took 3513.63 times longer than the fastest. This could mean that an intermediate result is being cached 
10000 loops, best of 3: 25 µs per loop


### Min/argmin
Use these functions judiciously. Never iterate through your matrix to find the smallest entry one. 

In [13]:
n,m = 10,6
X = np.random.randn(n,m)
X.argmin(axis=1)
X.min(axis=0);

### The log trick
You will need this to get well-conditioned numbers when computing probabilities. Suppose we have a vector of values $a$ and we need to compute $\exp(a_i)/\sum_{j}\exp(a_j)$. Computing this directly when $a$ is a very large negative number can pose numerical problems, since everything is 0. 

In [14]:
n=5
a = -np.ones(5)*(1e10)
np.exp(a)/np.exp(a).sum()

array([ nan,  nan,  nan,  nan,  nan])

In [15]:
-np.exp(-1e10)

-0.0

Then, note that
$$\frac{\exp(a_i)}{\sum_{j}\exp(a_j)} = \frac{\exp(a_i)}{\sum_{j}\exp(a_j)}\cdot \frac{\exp(-b)}{\exp(-b)} = \frac{\exp(a_i-b)}{\sum_{j}\exp(a_j-b)}$$
holds for any number $b$. It is common to pick b = \text{max}(a)$, so that at least one term in the resulting probability vector is 1. 

In [16]:
n=5
a = -np.ones(5)*(1e10)
b = a.max()
np.exp(a-b)/np.exp(a-b).sum()

array([ 0.2,  0.2,  0.2,  0.2,  0.2])

## Extra Stuff
Here's a few extra things that may help you with your contests. 

### Decaying learning rate in gradient descent. 
Recall that for gradient descent, we just apply a constant learning rate from a number of iterations. Consider the simple example $y = x^2$, and experiment with the learning rate: 

In [17]:
def y(x): 
    return x*x
def g(x): 
    return 0.5*x
lr = 50
niters= 100
x = 20

for i in range(niters):
    x -= g(x)*lr
print x

2.09968510225e+139


Depending on the size of the learning rate, this gradient descent may blow up. Furthermore, in some problems, if you run for too many iterations, a constant sized learning rate that is normally OK becomes too large. Thus, we introduce the idea of a decaying learning rate: every time our objective doesn't decrease, we reduce the learning rate by a factor of $\beta$ until it does. In practice, $\beta = 0.9$ works quite well. 

In [18]:
beta = 0.9
lr = 100
niters= 100
x = 20
for i in range(niters):
    x0 = x
    y0 = y(x)
    x = x0 - g(x)*lr
    while (y0 < y(x)):
        lr *= beta
        x = x0 - g(x)*lr
print x

3.72928978033


### Earliy stopping conditions for gradient descent
By doing so, you can stop adjusting the number of iterations for each particular problem and just pick one that is large enough.  If you want to remove even that condition, you can include an early stopping condition. For gradient descent, a simple condition is to just stop when the gradient is too small (since no progress will be made anyways): 

In [19]:
beta = 0.9
lr = 50
niters= 1000
x = 20
for i in range(niters):
    if g(x)*lr < 1e-8:
        break
    x0 = x
    y0 = y(x)
    x = x0 - g(x)*lr
    while (y0 < y(x)):
        lr *= beta
        x = x0 - g(x)*lr
print x,i

2.64884105353e-07 488


Then, you select `niters` to be as long as you are willing to wait, and if it terminates early, you save some time and don't need to tune as many parameters. 

### Getting combinations for median trick
If you decide to use RBF features you'll find that in order to use the median trick, you need to iterate over all pairs of centers. You can do this by using the `itertools.combinations` function:

In [20]:
import itertools
[c for c in itertools.combinations(range(6), 2)]

[(0, 1),
 (0, 2),
 (0, 3),
 (0, 4),
 (0, 5),
 (1, 2),
 (1, 3),
 (1, 4),
 (1, 5),
 (2, 3),
 (2, 4),
 (2, 5),
 (3, 4),
 (3, 5),
 (4, 5)]